In [3]:
# The goal is to produce a points predictor for players in the FPL. We will then use this to construct a (hopefully) winning
# team. Data can be found at https://github.com/vaastav/Fantasy-Premier-League/

In [129]:
# We begin by importing the standard libraries

import bs4
import numpy as np
import pandas as pd
import random
import requests
from io import StringIO


In [5]:
# We import the data
data_main = pd.read_csv('C:\\Users\jonat\OneDrive\Documents\Projects\Fantasy Premier League\Data\merged_cleaned_seasons.csv', low_memory = False)

In [51]:
print('Seasons : {0}'.format(data_main['season_x'].unique()))
seasons = list(data_main['season_x'].unique())

# We have data from six seasons. Before splitting the data into training and testing sets we have some data manipulation to do.

Seasons : ['2016-17' '2017-18' '2018-19' '2019-20' '2020-21' '2021-22']


In [29]:
# We first need to clean the names by removing all accents. We use the unidecode module
import unidecode

data_main['name'] = [unidecode.unidecode(name) for name in data_main['name']]

In [30]:
# Fix name entries for Bernado Silva. We look for which was used most recently.

print(data_main.loc[data_main['name'] == 'Bernardo Fernandes Da Silva Junior'].season_x.unique())
print(data_main.loc[data_main['name'] == 'Bernardo Fernandes da Silva Junior'].season_x.unique())

['2021-22']
['2018-19' '2019-20' '2020-21']


In [32]:
data_main.loc[data_main['name'] == 'Bernardo Fernandes Da Silva Junior', 'name'] = 'Bernardo Fernandes da Silva Junior'

In [33]:
# We want to construct a dataframe that has the first column as the response variable and the other columns are the covariates.

group_players_season = data_main.groupby(by=['name', 'season_x'])

# Look for instances where a name in a single season is associated to multiple 'element' values.
multi_element_instances = []
for (name, group) in group_players_season:
    if len(group.element.unique()) != 1:
        multi_element_instances.append(name)
        
print(multi_element_instances)

[('Alvaro Fernandez', '2021-22'), ('Ben Davies', '2020-21'), ('Ben Davies', '2021-22'), ('Danny Ward', '2018-19')]


In [34]:
# We see that these are instances where there are multiple players with the same name in the league. 
duplicate_names = []
for key in multi_element_instances:
    print(key, group_players_season.get_group(key).team_x.unique())
    duplicate_names.append(key[0])
    
duplicate_names = set(duplicate_names)
print(duplicate_names)

('Alvaro Fernandez', '2021-22') ['Brentford' 'Man Utd']
('Ben Davies', '2020-21') ['Spurs' 'Liverpool']
('Ben Davies', '2021-22') ['Liverpool' 'Spurs']
('Danny Ward', '2018-19') [nan]
{'Alvaro Fernandez', 'Danny Ward', 'Ben Davies'}


In [35]:
# Check what happened to Danny Ward in the 2018-19 season. Answer: One of these is the goalkeeper for Leicester City, the other
# is a winger for Cardiff City.

danny_ward_df = group_players_season.get_group(('Danny Ward', '2018-19'))
elements = danny_ward_df.element.unique()
print(elements)
for element in elements:
    print(danny_ward_df.loc[danny_ward_df.element == element].minutes.describe())
    
# From the relevant wikipedia pages we find that Danny Ward (Leicester) failed to make a single appearance in the 2018-19
# season and therefore we conclude that this is Danny Ward corresponding to element 457. We therefore fix the position of
# Danny Ward 105 from GK to FWD

data_main.loc[(data_main['name'] == 'Danny Ward') & (data_main['season_x'] == '2018-19') & (data_main['element'] == 105), 'position'] = 'FWD'

[105 457]
count    38.000000
mean     11.447368
std      22.347014
min       0.000000
25%       0.000000
50%       0.000000
75%      10.500000
max      83.000000
Name: minutes, dtype: float64
count    38.0
mean      0.0
std       0.0
min       0.0
25%       0.0
50%       0.0
75%       0.0
max       0.0
Name: minutes, dtype: float64


In [36]:
# Question: How do we ensure that we are comparing the same players across seasons?
#
# We know that, having taken into account the four instances noted above, there are no examples of players with the same names
# playing in the same season. So the question is: do we have players with the same name playing at different times? Does this
# even matter? We can apply some filters to potentially reduce further the chances of this occuring. We can say that if a player
# is only registered for one position then that is likely to be the same player.

players_group = data_main.groupby(by = ['name'])

for (name, data) in players_group:
    if len(data.position.unique()) != 1:
        print('{}: {}'.format(name, ', '.join(data.position.unique())))
        
# We see that these are mostly fine and are just multi-positional players being switched to a new primary position. The only
# clearly incorrect ones (interestingly) have been picked up earlier since they occurred in the same season.

Ainsley Maitland-Niles: DEF, MID
Allan Saint-Maximin: MID, FWD
Alvaro Fernandez: GK, DEF
Cheikhou Kouyate: MID, DEF
Danny Ward: GK, FWD
Fernando Luiz Rosa: DEF, MID
Kaine Hayden: MID, DEF
Matt Ritchie: MID, DEF
Nathan Broadhead: MID, FWD
Pierre-Emerick Aubameyang: MID, FWD
Stuart Dallas: DEF, MID


In [37]:
# We now begin the process of giving each player a unique identifier.

names = [name for name in data_main.name.unique() if name not in duplicate_names]
player_id_dict = dict(zip(names, range(len(names))))

data_main['player_id'] = [player_id_dict[name] if name not in duplicate_names else None for name in data_main.name]

In [65]:
# We now manually add the values for the names with more than one player associated to them.

ben_davies_id_1 = data_main.player_id.max() + 1
ben_davies_id_2 = data_main.player_id.max() + 2
alvaro_fernandez_id_1 = data_main.player_id.max() + 3
alvaro_fernandez_id_2 = data_main.player_id.max() + 4
danny_ward_id_1 = data_main.player_id.max() + 5
danny_ward_id_2 = data_main.player_id.max() + 6

# Setting player ids for Ben Daviess
data_main.loc[((data_main['name'] == 'Ben Davies') & (data_main['season_x'].isin(seasons[0:4]))), 'player_id'] = ben_davies_id_1
data_main.loc[((data_main['name'] == 'Ben Davies') & (data_main['team_x'] == 'Spurs')), 'player_id'] = ben_davies_id_1
data_main.loc[((data_main['name'] == 'Ben Davies') & (data_main['team_x'] == 'Liverpool')), 'player_id'] = ben_davies_id_2

# Setting player ids for Alvaro Fernandezs
data_main.loc[((data_main['name'] == 'Alvaro Fernandez') & (data_main['team_x'] == 'Brentford')), 'player_id'] = alvaro_fernandez_id_1
data_main.loc[((data_main['name'] == 'Alvaro Fernandez') & (data_main['team_x'] == 'Man Utd')), 'player_id'] = alvaro_fernandez_id_2

# Setting player ids for Danny Wards
data_main.loc[((data_main['name'] == 'Danny Ward') & (data_main['position'] == 'GK')), 'player_id'] = danny_ward_id_1
data_main.loc[((data_main['name'] == 'Danny Ward') & (data_main['position'] == 'FWD')), 'player_id'] = danny_ward_id_2

In [74]:
col_names = data_main.columns
print(col_names)

Index(['season_x', 'name', 'position', 'team_x', 'assists', 'bonus', 'bps',
       'clean_sheets', 'creativity', 'element', 'fixture', 'goals_conceded',
       'goals_scored', 'ict_index', 'influence', 'kickoff_time', 'minutes',
       'opponent_team', 'opp_team_name', 'own_goals', 'penalties_missed',
       'penalties_saved', 'red_cards', 'round', 'saves', 'selected',
       'team_a_score', 'team_h_score', 'threat', 'total_points',
       'transfers_balance', 'transfers_in', 'transfers_out', 'value',
       'was_home', 'yellow_cards', 'GW', 'player_id'],
      dtype='object')


In [77]:
# Create test dataframe
data_test = data_main.loc[data_main['season_x'].isin(seasons[0:4])]

In [119]:
# Check when we have non-null values in team_x
print(data_main.loc[data_main['team_x'].isna(), 'season_x'].unique())

['2016-17' '2017-18' '2018-19' '2019-20']


In [130]:
# Import team data for players for 16/17, 17/18, 18/19, 19/20

url1 = 'https://raw.githubusercontent.com/vaastav/Fantasy-Premier-League/master/data/master_team_list.csv'
resp = requests.get(url1)

team_id_data = pd.read_csv(StringIO(resp.text), sep = ',', low_memory = False, index_col = 0)

players_raw_1617_url = 'https://raw.githubusercontent.com/vaastav/Fantasy-Premier-League/master/data/2016-17/players_raw.csv'
players_raw_1718_url = 'https://raw.githubusercontent.com/vaastav/Fantasy-Premier-League/master/data/2017-18/players_raw.csv'
players_raw_1819_url = 'https://raw.githubusercontent.com/vaastav/Fantasy-Premier-League/master/data/2018-19/players_raw.csv'
players_raw_1920_url = 'https://raw.githubusercontent.com/vaastav/Fantasy-Premier-League/master/data/2019-20/players_raw.csv'

resp1617 = requests.get(players_raw_1617_url)
resp1718 = requests.get(players_raw_1718_url)
resp1819 = requests.get(players_raw_1819_url)
resp1920 = requests.get(players_raw_1920_url)

players_raw_1617 = pd.read_csv(StringIO(resp1617.text), sep = ',', low_memory = False)
players_raw_1718 = pd.read_csv(StringIO(resp1718.text), sep = ',', low_memory = False)
players_raw_1819 = pd.read_csv(StringIO(resp1819.text), sep = ',', low_memory = False)
players_raw_1920 = pd.read_csv(StringIO(resp1920.text), sep = ',', low_memory = False)

In [138]:
# Create name column in raw data dataframes
players_raw_1617['name'] = players_raw_1617['first_name'] + ' ' + players_raw_1617['second_name']
players_raw_1718['name'] = players_raw_1718['first_name'] + ' ' + players_raw_1718['second_name']
players_raw_1819['name'] = players_raw_1819['first_name'] + ' ' + players_raw_1819['second_name']
players_raw_1920['name'] = players_raw_1920['first_name'] + ' ' + players_raw_1920['second_name']

# Remove accents from names
players_raw_1617['name'] = [unidecode.unidecode(name) for name in players_raw_1617['name']]
players_raw_1718['name'] = [unidecode.unidecode(name) for name in players_raw_1718['name']]
players_raw_1819['name'] = [unidecode.unidecode(name) for name in players_raw_1819['name']]
players_raw_1920['name'] = [unidecode.unidecode(name) for name in players_raw_1920['name']]

In [162]:
# Import team id list
url1 = 'https://raw.githubusercontent.com/vaastav/Fantasy-Premier-League/master/data/master_team_list.csv'
resp = requests.get(url1)

team_id_data = pd.read_csv(StringIO(resp.text), sep = ',', low_memory = False, index_col = 0)
team_id_data['season_x'] = team_id_data.index

In [144]:
data_test['team_name'] = None

for index, season, name in zip(range(data_test.shape[0]), data_test['season_x'], data_test['name']):
    if season == '2016-17':
        team_id = players_raw_1617.loc[players_raw_1617['name'] == name, 'team']
        team_name = team_id_data.loc[(team_id_data['season_x'] == season) & (team_id_data['team'] == team_id), 'team_name']
        data_test.iloc[index, team_id_data.columns.]
    elif season == '2017-18':
        team_id = players_raw_1718.loc[players_raw_1718['name'] == name, 'team']
        team_name = team_id_data.loc[(team_id_data['season_x'] == season) & (team_id_data['team'] == team_id), 'team_name']
    elif season == '2018-19':
        team_id = players_raw_1819.loc[players_raw_1819['name'] == name, 'team']
        team_name = team_id_data.loc[(team_id_data['season_x'] == season) & (team_id_data['team'] == team_id), 'team_name']
    elif season == '2019-20':
        team_id = players_raw_1920.loc[players_raw_1920['name'] == name, 'team']
        team_name = team_id_data.loc[(team_id_data['season_x'] == season) & (team_id_data['team'] == team_id), 'team_name']

2016-17
Aaron Cresswell
2016-17
Aaron Lennon
2016-17
Aaron Ramsey
2016-17
Abdoulaye Doucoure
2016-17
Adam Forshaw
2016-17
Adam Lallana
2016-17
Adrian San Miguel del Castillo
2016-17
Alex Iwobi
2016-17
Alex McCarthy
2016-17
Alex Oxlade-Chamberlain
2016-17
Andreas Pereira
2016-17
Andrew Robertson
2016-17
Andre Gray
2016-17
Andros Townsend
2016-17
Andy Carroll
2016-17
Angelo Ogbonna
2016-17
Anthony Martial
2016-17
Arthur Masuaku
2016-17
Ashley Barnes
2016-17
Ashley Young
2016-17
Bamidele Alli
2016-17
Benjamin Chilwell
2016-17
Ben Davies
2016-17
Ben Foster
2016-17
Ben Gibson
2016-17
Ben Mee
2016-17
Branislav Ivanovic
2016-17
Callum Wilson
2016-17
Calum Chambers
2016-17
Cameron Carter-Vickers
2016-17
Charlie Austin
2016-17
Cheikhou Kouyate
2016-17
Christian Benteke
2016-17
Christian Eriksen
2016-17
Christian Fuchs
2016-17
Christian Kabasele
2016-17
Chris Smalling
2016-17
Connor Wickham
2016-17
Craig Cathcart
2016-17
Craig Dawson
2016-17
Cedric Soares
2016-17
Cesar Azpilicueta
2016-17
Daniel

Cameron Carter-Vickers
2016-17
Charlie Austin
2016-17
Cheikhou Kouyate
2016-17
Christian Benteke
2016-17
Christian Eriksen
2016-17
Christian Fuchs
2016-17
Christian Kabasele
2016-17
Chris Smalling
2016-17
Claudio Bravo
2016-17
Connor Wickham
2016-17
Craig Cathcart
2016-17
Craig Dawson
2016-17
Cedric Soares
2016-17
Cesar Azpilicueta
2016-17
Daniel Amartey
2016-17
Daniel James
2016-17
Danny Ings
2016-17
Danny Rose
2016-17
Danny Welbeck
2016-17
Dan Gosling
2016-17
Darren Randolph
2016-17
David de Gea
2016-17
David Luiz Moreira Marinho
2016-17
DeAndre Yedlin
2016-17
Demarai Gray
2016-17
Divock Origi
2016-17
Dominic Calvert-Lewin
2016-17
Eldin Jakupovic
2016-17
Eric Bailly
2016-17
Eric Dier
2016-17
Erik Lamela
2016-17
Erik Pieters
2016-17
Fabian Delph
2016-17
Federico Fernandez
2016-17
Fernando Luiz Rosa
2016-17
Fraser Forster
2016-17
Gary Cahill
2016-17
Georginio Wijnaldum
2016-17
Granit Xhaka
2016-17
Gylfi Sigurdsson
2016-17
Hal Robson-Kanu
2016-17
Harrison Reed
2016-17
Harry Kane
2016-17

Odion Ighalo
2016-17
Ola Aina
2016-17
Oleksandr Zinchenko
2016-17
Oliver McBurnie
2016-17
Olivier Giroud
2016-17
Oriol Romeu Vidal
2016-17
Patrick Bamford
2016-17
Patrick van Aanholt
2016-17
Paulo Gazzaniga
2016-17
Paul Pogba
2016-17
Phil Bardsley
2016-17
Phil Jagielka
2016-17
Phil Jones
2016-17
Pierre-Emile Hojbjerg
2016-17
Raheem Sterling
2016-17
Rekeem Harper
2016-17
Riyad Mahrez
2016-17
Robert Kenedy Nunes do Nascimento
2016-17
Roberto Firmino
2016-17
Robert Snodgrass
2016-17
Rob Holding
2016-17
Romelu Lukaku
2016-17
Ross Barkley
2016-17
Ruben Loftus-Cheek
2016-17
Ryan Bertrand
2016-17
Ryan Fraser
2016-17
Sadio Mane
2016-17
Salomon Rondon
2016-17
Sam Byram
2016-17
Sam Field
2016-17
Scott Dann
2016-17
Seamus Coleman
2016-17
Sergio Aguero
2016-17
Sergio Romero
2016-17
Shane Long
2016-17
Shkodran Mustafi
2016-17
Sofiane Boufal
2016-17
Theo Walcott
2016-17
Timothy Fosu-Mensah
2016-17
Toby Alderweireld
2016-17
Tom Cleverley
2016-17
Tom Davies
2016-17
Tom Heaton
2016-17
Trent Alexander-A

2016-17
Joshua King
2016-17
Josh Maja
2016-17
Juan Mata
2016-17
Kasper Schmeichel
2016-17
Kelechi Iheanacho
2016-17
Kevin De Bruyne
2016-17
Kevin Long
2016-17
Kieran Gibbs
2016-17
Kieran Trippier
2016-17
Kurt Zouma
2016-17
Kyle Walker
2016-17
Lee Grant
2016-17
Lukasz Fabianski
2016-17
Luke Shaw
2016-17
Lys Mousset
2016-17
Mamadou Sakho
2016-17
Manuel Lanzini
2016-17
Marcos Alonso
2016-17
Marcos Rojo
2016-17
Marcus Rashford
2016-17
Marc Albrighton
2016-17
Mark Noble
2016-17
Martin Kelly
2016-17
Mason Holgate
2016-17
Matej Vydra
2016-17
Matthew Lowton
2016-17
Matt Phillips
2016-17
Matt Targett
2016-17
Mesut Ozil
2016-17
Michael Keane
2016-17
Michail Antonio
2016-17
Michy Batshuayi
2016-17
Moussa Sissoko
2016-17
N'Golo Kante
2016-17
Nampalys Mendy
2016-17
Nathaniel Chalobah
2016-17
Nathaniel Clyne
2016-17
Nathan Ake
2016-17
Nathan Redmond
2016-17
Neil Taylor
2016-17
Nemanja Matic
2016-17
Nick Pope
2016-17
Nicolas Otamendi
2016-17
Odion Ighalo
2016-17
Ola Aina
2016-17
Oleksandr Zinchenko
2

Troy Deeney
2016-17
Tyrone Mings
2016-17
Virgil van Dijk
2016-17
Wayne Hennessey
2016-17
Wes Morgan
2016-17
Wilfred Ndidi
2016-17
Wilfried Zaha
2016-17
Willian Borges Da Silva
2016-17
Willy Caballero
2016-17
Winston Reid
2016-17
Xherdan Shaqiri
2016-17
Aaron Cresswell
2016-17
Aaron Lennon
2016-17
Aaron Wan-Bissaka
2016-17
Abdoulaye Doucoure
2016-17
Adama Traore
2016-17
Adam Forshaw
2016-17
Adam Lallana
2016-17
Ademola Lookman
2016-17
Adrian San Miguel del Castillo
2016-17
Alfie Mawson
2016-17
Andrew Robertson
2016-17
Andre Gray
2016-17
Andros Townsend
2016-17
Andy Carroll
2016-17
Angelo Ogbonna
2016-17
Arthur Masuaku
2016-17
Ashley Barnes
2016-17
Ashley Fletcher
2016-17
Ashley Westwood
2016-17
Bamidele Alli
2016-17
Benjamin Chilwell
2016-17
Ben Davies
2016-17
Ben Foster
2016-17
Ben Gibson
2016-17
Ben Mee
2016-17
Ben Woodburn
2016-17
Branislav Ivanovic
2016-17
Callum Wilson
2016-17
Calum Chambers
2016-17
Cameron Carter-Vickers
2016-17
Cheikhou Kouyate
2016-17
Christian Benteke
2016-17
C

...

2021-22
Angus Gunn
2021-22
Aaron Ramsdale
2021-22
Jack Stephens
2021-22
Francisco Femenia Far
2021-22
Will Norris
2021-22
Michail Antonio
2021-22
Malang Sarr
2021-22
Tony Springett
2021-22
Ruben Diogo da Silva Neves
2021-22
Benjamin Chrisene
2021-22
Michael Keane
2021-22
Bernd Leno
2021-22
Armstrong Oko-Flex
2021-22
Robert Sanchez
2021-22
Kasey McAteer
2021-22
Jeffrey Schlupp
2021-22
Harvey Barnes
2021-22
Nathan Tella
2021-22
Harry Lewis
2021-22
Yoane Wissa
2021-22
Pierre Lees-Melou
2021-22
Adrian San Miguel del Castillo
2021-22
Fabio Silva
2021-22
Odsonne Edouard
2021-22
Kwadwo Baah
2021-22
Martin Dubravka
2021-22
John Ruddy
2021-22
Anthony Gordon
2021-22
Nicolas Pepe
2021-22
Jason Steele
2021-22
Imran Louza
2021-22
Dean Henderson
2021-22
Paul Dummett
2021-22
Jordan Hugill
2021-22
Tom Heaton
2021-22
Vontae Daley-Campbell
2021-22
Dane Scarlett
2021-22
Matteo Guendouzi
2021-22
Odeluga Offiah
2021-22
Ryan Fraser
2021-22
Max Aarons
2021-22
Phil Jones
2021-22
Olivier Giroud
2021-22
Callum 

Robert Elliot
2021-22
Joshua King
2021-22
Joshua King
2021-22
Richarlison de Andrade
2021-22
Richarlison de Andrade
2021-22
Jamal Baptiste
2021-22
Filip Marschall
2021-22
Filip Marschall
2021-22
Sam Byram
2021-22
Sam Byram
2021-22
Danny Rose
2021-22
Danny Rose
2021-22
Julian Jeanvier
2021-22
Ederson Santana de Moraes
2021-22
Ederson Santana de Moraes
2021-22
Dion Sanderson
2021-22
Dion Sanderson
2021-22
Liam Cooper
2021-22
Liam Cooper
2021-22
Frederic Guilbert
2021-22
Frederic Guilbert
2021-22
Matt Targett
2021-22
James McAtee
2021-22
James McAtee
2021-22
Adama Traore
2021-22
Adama Traore
2021-22
Jorge Luiz Frello Filho
2021-22
Jorge Luiz Frello Filho
2021-22
Diogo Jota
2021-22
Diogo Jota
2021-22
Ilkay Gundogan
2021-22
Ilkay Gundogan
2021-22
Luke Shaw
2021-22
Armando Broja
2021-22
Ed Turns
2021-22
Nicolas Nkoulou
2021-22
Nicolas Nkoulou
2021-22
Stipe Perica
2021-22
Stipe Perica
2021-22
Emerson Palmieri dos Santos
2021-22
Emerson Palmieri dos Santos
2021-22
Daniel Chesters
2021-22
Isaac

2021-22
Martin Dubravka
2021-22
Vitalii Mykolenko
2021-22
Vitalii Mykolenko
2021-22
Nathaniel Clyne
2021-22
Luke Mbete
2021-22
Luke Mbete
2021-22
Lukasz Fabianski
2021-22
Gylfi Sigurdsson
2021-22
Gylfi Sigurdsson
2021-22
Yerry Mina
2021-22
Yerry Mina
2021-22
Nathan Collins
2021-22
Matteo Guendouzi
2021-22
Matteo Guendouzi
2021-22
Shandon Baptiste
2021-22
James Justin
2021-22
James Justin
2021-22
Conor Coventry
2021-22
Grant Hanley
2021-22
Grant Hanley
2021-22
Emiliano Martinez
2021-22
Emiliano Martinez
2021-22
Oriol Romeu Vidal
2021-22
Emil Krafth
2021-22
Christian Pulisic
2021-22
Christian Pulisic
2021-22
Jaroslaw Jach
2021-22
Isaac Price
2021-22
Isaac Price
2021-22
Tom Cleverley
2021-22
Tom Cleverley
2021-22
Alvaro Fernandez
2021-22
Caglar Soyuncu
2021-22
Caglar Soyuncu
2021-22
John Stones
2021-22
John Stones
2021-22
Viljami Sinisalo
2021-22
Viljami Sinisalo
2021-22
Pedro Lomba Neto
2021-22
Pedro Lomba Neto
2021-22
Danny Ings
2021-22
Danny Ings
2021-22
Emerson Aparecido Leite de Souz

2021-22
Tariqe Fosu-Henry
2021-22
Thomas Partey
2021-22
Karl Hein
2021-22
Francisco Femenia Far
2021-22
Maxwel Cornet
2021-22
Raul Jimenez
2021-22
Jarell Quansah
2021-22
Sean Longstaff
2021-22
Boubakary Soumare
2021-22
Hector Bellerin
2021-22
Emmanuel Dennis
2021-22
Lucas Torreira
2021-22
Nampalys Mendy
2021-22
Ryan Fraser
2021-22
Alex Kral
2021-22
Paul Pogba
2021-22
Josh Feeney
2021-22
Bertrand Traore
2021-22
Leandro Trossard
2021-22
Christian Norgaard
2021-22
Wesley Fofana
2021-22
Tommy Doyle
2021-22
Nemanja Matic
2021-22
Arthur Masuaku
2021-22
Bernard Anicio Caldeira Duarte
2021-22
Brandon Williams
2021-22
Kenny McLean
2021-22
Jeremy Ngakia
2021-22
Connor Roberts
2021-22
Sadio Mane
2021-22
Conor Bradley
2021-22
Edward Nketiah
2021-22
Jakub Moder
2021-22
Ben Davies
2021-22
Trevoh Chalobah
2021-22
Bali Mumba
2021-22
Enock Mwepu
2021-22
Theo Walcott
2021-22
Fabian Schar
2021-22
Mateusz Klich
2021-22
Che Adams
2021-22
Andriy Yarmolenko
2021-22
Onel Hernandez
2021-22
Benjamin Chilwell
20

Jonathan Castro Otto
2021-22
Patrik Gunnarsson
2021-22
Matthew Longstaff
2021-22
Saul Niguez
2021-22
James Tomkins
2021-22
Timo Werner
2021-22
David Raya Martin
2021-22
Nick Pope
2021-22
Ezri Konsa Ngoyo
2021-22
Odeluga Offiah
2021-22
Kristoffer Klaesson
2021-22
Gabriel Teodoro Martinelli Silva
2021-22
Christian Marques
2021-22
Heung-Min Son
2021-22
Jack Jenkins
2021-22
Shaqai Forde
2021-22
Lewis Dobbin
2021-22
Jack Cork
2021-22
Domingos Quina
2021-22
Aaron Ramsey
2021-22
Patrick Cutrone
2021-22
Jacob Ramsey
2021-22
Leo Fuhr Hjelde
2021-22
Nathan Ake
2021-22
Jonjoe Kenny
2021-22
Dennis Praet
2021-22
Joseph Willock
2021-22
Angelo Ogbonna
2021-22
Pablo Hernandez Dominguez
2021-22
Reiss Nelson
2021-22
Rob Holding
2021-22
Harry Kane
2021-22
Troy Deeney
2021-22
Lucas De Bolle
2021-22
Seamus Coleman
2021-22
Harvey Barnes
2021-22
Sergio Reguilon
2021-22
Timothy Castagne
2021-22
Joachim Andersen
2021-22
Bailey Peacock-Farrell
2021-22
Tom Heaton
2021-22
Pierluigi Gollini
2021-22
Josh Brownhill


In [173]:
# team_id_data.iloc[1, team_id_data.columns.'team']
list(team_id_data.columns).index('team_name')

1